In [4]:
!pip install transformers
!pip install pysnooper
import os 
import pandas as pd
import torch
import sys
import os
from collections import Counter

from torch.utils.data import Dataset
from transformers import BertTokenizer
import torch
import pysnooper
import spacy 
  
# Load English tokenizer, tagger,  
# parser, NER and word vectors 

import pandas as pd
from google.colab import drive
drive.mount('/content/drive')
nlp = spacy.load("en_core_web_sm") 

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
import sys
!test -d bertviz_repo || git clone https://github.com/jessevig/bertviz bertviz_repo
if not 'bertviz_repo' in sys.path:
  sys.path += ['bertviz_repo']

# import packages
from transformers import BertTokenizer, BertModel
from bertviz import head_view

# 在 jupyter notebook 裡頭顯示 visualzation 的 helper
def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.8/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

In [6]:
#@titl
PRETRAINED_MODEL_NAME = "bert-base-uncased"  # 指定 BERT-BASE 預訓練模型

# 取得此預訓練模型所使用的 tokenizer
tokenizer = BertTokenizer.from_pretrained(PRETRAINED_MODEL_NAME)

# clear_output()
print("PyTorch 版本：", torch.__version__)


PyTorch 版本： 1.4.0


In [7]:
df = pd.read_csv('./drive/My Drive/data_nlp/'+ 'train' + '.tsv', sep='\t').fillna("")

print("預測樣本數：", len(df))
type(df.label[3])
type(df.iloc[1, :1].values)

預測樣本數： 67349


numpy.ndarray

In [0]:
# path = os.path.join(absFilePath, '../'+ 'datasetSentences' + '.txt')
from torch.utils.data import Dataset
import re
from random import sample

class Prepro_Data(Dataset):
    
    def __init__(self, tokenizer, nlp, text_file_name, max_length=30):

        self.text, self.label = self.preprocess(text_file_name, max_length)
        
        self.tokenizer = tokenizer
        self.nlp = nlp


    def __getitem__(self, idx, sign=None):
        
        text, label = self.text[idx], self.label[idx]
    
        # tokens_old = self.tokenizer.tokenize(text)
        tokens = text.split()
        # print('tokens', tokens, tokens_new)
        # word_pieces = ['[CLS]'] + tokens_old
        word_pieces = ['[CLS]'] + tokens   
        # print('word_pieces', word_pieces)
        # print('word_pieces', word_pieces_comp)
        if sign == 'Augment':
            
            for idx, token in enumerate(tokens):

                if token.pos_ == 'VERB':
                    tokens[idx] = '[MASK]'
                
        ids = self.tokenizer.convert_tokens_to_ids(tokens)
        label_tensor = torch.tensor(label.item())
        tokens_tensor = torch.tensor(ids)
        segments_tensor = torch.zeros_like(tokens_tensor)  # (1, seq_len)

        return (tokens_tensor, label_tensor)
    
    def  __len__(self):      
        return len(self.text)

    @staticmethod
    def load_data(FILE_NAME):

      df = pd.read_csv('./drive/My Drive/Data/SST-2/'+ FILE_NAME + '.tsv', sep='\t').fillna("")

      return df

    @classmethod
    def preprocess(clf, FILE_NAME, max_length):
      
      SAMPLE_FRAC = 0.01
      data = clf.load_data(FILE_NAME)
      if FILE_NAME == 'test':
        text = data.iloc[:, :1].values
        label = None

      else:
        data = data.sample(frac=SAMPLE_FRAC, random_state=9527)
        empty_title = ((data['sentence'].isnull()) \
               | (data['sentence'] == '') \
               | (data['sentence'] == '0'))
        data = data[~empty_title]
        data = data[~(data.sentence.apply(lambda x : len(x)) > max_length)]
        
        text, label = data.iloc[:, 0].values, data.iloc[:, 1].values
      return text, label

trainset = Prepro_Data(tokenizer = tokenizer, nlp = nlp, text_file_name = 'train')    

In [0]:
# df = Prepro_Data.load_data('test')
# trainset[1]

In [10]:
from torch.utils.data import DataLoader
from torch.nn.utils.rnn import pad_sequence

def create_mini_batch(samples):

    tokens_tensors = [s[0] for s in samples]
    # segments_tensors = [s[1] for s in samples]
    
    if samples[0][1] is not None:
        label_ids = torch.stack([s[1] for s in samples])
        
    else:
        label_ids = None
        
    tokens_tensors = pad_sequence(tokens_tensors,
                                 batch_first=True)
#     print('tokens_tensors', tokens_tensors)
    masks_tensors = torch.zeros(tokens_tensors.shape,
                               dtype=torch.long)
    masks_tensors = masks_tensors.masked_fill(tokens_tensors != 0, 1)
    return tokens_tensors, masks_tensors, label_ids

BATCH_SIZE = 64

trainloader = DataLoader(trainset, batch_size=BATCH_SIZE, collate_fn=create_mini_batch)

trainloader
    
    

In [11]:
#@titl
from transformers import BertForSequenceClassification

NUM_LABELS = 2
model = BertForSequenceClassification.from_pretrained(PRETRAINED_MODEL_NAME,
                                                     num_labels=NUM_LABELS)
print("""
name            module
----------------------""")
for name, module in model.named_children():
    if name == "bert":
        for n, _ in module.named_children():
            print(f"{name}:{n}")
    else:
        print("{:15} {}".format(name, module))






name            module
----------------------
bert:embeddings
bert:encoder
bert:pooler
dropout         Dropout(p=0.1, inplace=False)
classifier      Linear(in_features=768, out_features=2, bias=True)


In [15]:

def get_predictions(model, dataloader, compute_acc=False):
    predictions = None
    correct = 0
    total = 0
    
    with torch.no_grad():
        
        for data in dataloader:
            if next(model.parameters()).is_cuda:
                data = [t.to('cuda:0') for t in data if t is not None]
                
            tokens_tensors, masks_tensors = data[:2]
            # print('token_tensors', tokens_tensors)
            # print('masks_tensors', masks_tensors)

            outputs = model(input_ids=tokens_tensors,
                          #  token_type_ids=segments_tensors,
                           attention_mask=masks_tensors)

            # print('outputs', outputs)

            logits = outputs[0]
            # print('logits', logits)

            _, pred = torch.max(logits.data, 1)
                
            if compute_acc:
                labels = data[2]
                
                total += labels.size(0)
#                 print('total', total)

                correct += (pred == labels).sum().item()

            if predictions is None:
                predictions = pred

            else:

                predictions = torch.cat((predictions, pred))
                    
        if compute_acc:
            acc = correct / total
            return predictions, acc

        return predictions
    
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print(device)
model = model.to(device)
_, acc = get_predictions(model, trainloader, compute_acc=True)
print('classification acc:', acc)


cuda:0
classification acc: 0.4562043795620438


In [16]:
%%time

model.train()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-5)
EPOCHS = 50


for epoch in range(EPOCHS):
    
    running_loss = 0.0

    
    for data in trainloader:
        
        tokens_tensors, masks_tensors, labels = [t.to(device) for t in data]
        
        optimizer.zero_grad()
        
        outputs = model(input_ids=tokens_tensors,
                        # token_type_ids=segments_tensors,
                        attention_mask=masks_tensors,
                        labels=labels)
        
        loss = outputs[0]
        
        loss.backward()
        # loss.detach()
        optimizer.step()
        
        running_loss += loss.item()
        loss.detach()
    # torch.cuda.empty_cache() 
    _, acc = get_predictions(model, trainloader, compute_acc=True)
    
    if (epoch + 1) % 5 == 0:
      print('[epoch %d] loss: %.3f, acc:%.3f' % (epoch + 1, running_loss, acc))

[epoch 5] loss: 3.257, acc:0.584
[epoch 10] loss: 3.174, acc:0.617
[epoch 15] loss: 3.014, acc:0.679
[epoch 20] loss: 2.641, acc:0.715
[epoch 25] loss: 2.216, acc:0.792
[epoch 30] loss: 1.534, acc:0.869
[epoch 35] loss: 1.276, acc:0.872
[epoch 40] loss: 0.907, acc:0.901
[epoch 45] loss: 0.880, acc:0.920
[epoch 50] loss: 0.820, acc:0.934
CPU times: user 30.4 s, sys: 11.4 s, total: 41.8 s
Wall time: 42.2 s


In [17]:
%%time
testset = Prepro_Data(tokenizer, nlp, 'test')
testloader = DataLoader(testset, batch_size=64, collate_fn=create_mini_batch)
testloader
predictions = get_predictions(model, trainloader)
df = pd.DataFrame({"predicted": predictions.tolist()})
df['predicted'] = df.predicted
df1 = pd.concat([trainset.load_data('test'), df.loc[:, 'predicted']], axis=1)
# disagreed_tp = ((df1.label == 'disagreed') & \
#                 (df1.label == df1.predicted) & \
#                 (df1.text_a.apply(lambda x: True if len(x) < 10 else False)))
# df1[disagreed_tp].head()
# print(predictions)


CPU times: user 139 ms, sys: 30.6 ms, total: 170 ms
Wall time: 177 ms


In [19]:
# model_version = "bert-base-uncased"
finetuned_model = BertModel.from_pretrained(PRETRAINED_MODEL_NAME, output_attentions=True, state_dict=model.state_dict())

sentence = "none of this violates the letter of behan 's book , but missing is its spirit , its ribald , full-throated humor ."
inputs = tokenizer.encode_plus(sentence, return_tensors='pt', add_special_tokens=True)
token_type_ids = inputs['token_type_ids']
input_ids = inputs['input_ids']
attention = finetuned_model(input_ids, token_type_ids=token_type_ids)[-1]
input_id_list = input_ids[0].tolist()
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
call_html()
head_view(attention, tokens)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [31]:
finetuned_model = BertModel.from_pretrained(PRETRAINED_MODEL_NAME, output_attentions=True)

sentence = 'probably the best case for christianity since chesterton and lewis .'
inputs = tokenizer.encode_plus(sentence, return_tensors='pt', add_special_tokens=True)
token_type_ids = inputs['token_type_ids']
input_ids = inputs['input_ids']
attention = finetuned_model(input_ids, token_type_ids=token_type_ids)[-1]
input_id_list = input_ids[0].tolist()
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
call_html()
head_view(attention, tokens)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>